In [104]:
import pandas as pd
import os
import torch
import json
import re
import ast
import warnings
import pandas as pd
warnings.filterwarnings('ignore')
os.environ['HF_HOME'] = '/raid/abhilash/huggingfacecache/huggingface/hub/'

from transformers import pipeline, AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig, AutoModel
from fuzzywuzzy import fuzz
from sentence_transformers import SentenceTransformer, util
from tqdm import tqdm
from transformers.utils import logging
logging.set_verbosity_error() 

In [2]:
FCT_csv = 'reasoning_FCT.csv'
df = pd.read_csv(FCT_csv)

In [3]:
df

id          dataset  \
0      bc8659f4-3062-4f57-9e24-e32ad92a8d4e        headqa_en   
1      9fcf1ab0-387c-447a-ab6c-78367b5e5282        headqa_en   
2      0ac6c5c7-9826-441a-81d5-68478e6299bb  medqa_taiwan_en   
3      a6758ac9-7608-4866-bb00-c5e7b19917d5          medmcqa   
4      839de867-3100-4283-a219-ec349eee415f          medmcqa   
...                                     ...              ...   
18861  ebb8bf2a-1aec-4357-8c11-8763a023f0de        headqa_en   
18862  a714a188-4737-456d-b404-461625700e43  medqa_taiwan_en   
18863  34148baa-a617-4fea-9869-1159abfc994e        headqa_en   
18864  da49e7ab-a237-4882-8e10-185b981c5c32        headqa_en   
18865  a1e9f896-7310-45b7-a118-4cb8b194f583  medqa_taiwan_en   

                                                question  \
0      Which of the following structural elements is ...   
1      For what age group is the turtle technique ind...   
2      A 56-year-old man with hypertension, diabetes,...   
3      Which of the following is advantage of sub-mar...   
4                    Most impoant intracellular buffer ?   
...                                                  ...   
18861  He has to repeat the metabolic tests to a newb...   
18862  47 glomerular filter (Glomerular filtration ap...   
18863  When the protocol of a research project is ela...   
18864  One of the characteristics of the STEPPS progr...   
18865  The following related sacrococcygeal teratoma ...   

                                                 options  \
0      {'0': 'They are anilides with propyl group in ...   
1      {'0': 'Young children (Early Childhood Educati...   
2      {'0': '＜130/80 mmHg', '1': '150-160/90-95 mmHg...   
3      {'0': 'Cause less gingival shrinking', '1': 'C...   
4      {'0': 'Bicarbonate', '1': 'Albumin', '2': 'Pho...   
...                                                  ...   
18861  {'0': 'Ibuprofen oral', '1': 'Oral sucrose', '...   
18862  {'0': '\ue000 and \ue001', '1': '\ue001 and \u...   
18863  {'0': 'Define the objectives.', '1': 'Justify ...   
18864  {'0': 'It is an individual treatment.', '1': '...   
18865  {'0': 'By the cells of ectodermal and mesoderm...   

                                          correct_answer  correct_index  \
0       They are benzamides with methoxy group in ortho.              1   
1      Young children (Early Childhood Education and ...              0   
2                                           ＜130/80 mmHg              0   
3                          Cause less gingival shrinking              0   
4                                              Phosphate              2   
...                                                  ...            ...   
18861                                       Oral sucrose              1   
18862                                             and               2   
18863                             Define the objectives.              0   
18864                      Its exclusively group format.              2   
18865  Original Article (primitive streak) caused by ...              1   

      split_type  subject_name topic_name    year          exam_name  \
0            val  pharmacology        NaN  2015.0  Cuaderno_2015_1_F   
1           test    psychology        NaN  2016.0  Cuaderno_2016_1_P   
2           test           NaN        NaN     NaN                NaN   
3            val        Dental       None     NaN                NaN   
4           test    Physiology        NaN     NaN                NaN   
...          ...           ...        ...     ...                ...   
18861        val       nursery        NaN  2015.0  Cuaderno_2015_1_E   
18862       test           NaN        NaN     NaN                NaN   
18863       test      medicine        NaN  2017.0  Cuaderno_2017_1_M   
18864       test    psychology        NaN  2016.0  Cuaderno_2016_1_P   
18865        dev           NaN        NaN     NaN                NaN   

                                          student_answer  studen

In [4]:
model_name = "BioMistral/BioMistral-7B"  # Specify the name or path of the Mistral model
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map="balanced_low_0",
    trust_remote_code=True,
    use_cache=False,
    revision="main",
    torch_dtype=torch.bfloat16,
    # load_in_8bit=True,
    cache_dir="/raid/abhilash/huggingfacecache/huggingface/hub/"
).half().eval()

# Load the tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name, add_bos_token=True, trust_remote_code=True)

In [5]:
def generate(prompt):
    model_input = tokenizer(prompt, return_tensors="pt").to("cuda:"+str(3))
    output = model.generate(**model_input, max_new_tokens=200, repetition_penalty=1.15)
    answer = tokenizer.decode(output[0], skip_special_tokens=True)
    return answer

## DEFINE PROMPT TEMPLATES

In [6]:
few_shot_prompt_template = """As a medical teacher, you have the task of reviewing a medical student's answers to multiple-choice questions. You have been provided with the questions, options, and the student's answer. Carefully review the student's answer and provide a clear explanation on the correctness or incorrectness of their choice. Furthermore, explain why the other options are not the right answers.
Your output must be in the following JSON format: {'is_answer_correct': yes/no, 'answer': 'correct answer', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}
Examples: 
Input : {'Question': 'A child has ptosis and poor levator function. What surgery will you do?', 'Options': {'0': 'Levator muscle resection', '1': 'Mullerectomy', '2': 'Fasanella Servat surgery', '3': 'Frontalis suspension surgery'}, 'correct_answer': 'Frontalis suspension surgery'}
Output: {'is_answer_correct': 'yes', 'correct answer': 'Frontalis suspension surgery', 'why_correct': 'Frontalis suspension surgery is used for severe ptosis with poor levator muscle function. It allows the forehead to help elevate the eyelid.', 'why_others_incorrect': 'The other procedures, such as Levator muscle resection, Mullerectomy, and Fasanella Servat surgery, are used for cases of ptosis with better levator function.'}Stop Here

Input : {'Question': 'Chronic urethral obstruction due to benign prismatic hyperplasia can lead to the following change in kidney parenchyma?', 'Options': {'0': 'Hyperplasia', '1': 'Hyperophy', '2': 'Atrophy', '3': 'Dyplasia'}, 'correct_answer': 'Hyperophy'}
Output: {'is_answer_correct': 'no', 'correct answer': 'Atrophy', 'why_correct': 'Chronic urethral obstruction due to benign prostatic hyperplasia often leads to a backflow of urine, causing hydronephrosis. Over time, this may lead to atrophy of the kidney parenchyma.', 'why_others_incorrect': 'Hyperplasia, hyperophy, and dysplasia are not typically seen in the kidney as a result of chronic urethral obstruction due to benign prostatic hyperplasia.'}Stop Here
"""

zero_shot_prompt_template = """As a medical teacher, you have the task of reviewing a medical student's answers to multiple-choice questions. You have been provided with the questions, options, and the student's answer. Carefully review the student's answer and provide a clear explanation on the correctness or incorrectness of their choice. Furthermore, explain why the other options are not the right answers."
Your output must be in the following JSON format: {'is_answer_correct': yes/no, 'answer': 'correct answer', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}"
"""

In [7]:
print(few_shot_prompt_template)

As a medical teacher, you have the task of reviewing a medical student's answers to multiple-choice questions. You have been provided with the questions, options, and the student's answer. Carefully review the student's answer and provide a clear explanation on the correctness or incorrectness of their choice. Furthermore, explain why the other options are not the right answers.
Your output must be in the following JSON format: {'is_answer_correct': yes/no, 'answer': 'correct answer', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}
Examples: 
Input : {'Question': 'A child has ptosis and poor levator function. What surgery will you do?', 'Options': {'0': 'Levator muscle resection', '1': 'Mullerectomy', '2': 'Fasanella Servat surgery', '3': 'Frontalis suspension surgery'}, 'correct_answer': 'Frontalis suspension surgery'}
Output: {'is_answer_correct': 'yes', 'correct answer': 'Frontalis suspension surgery', 'why_correct

In [8]:
print(zero_shot_prompt_template)

As a medical teacher, you have the task of reviewing a medical student's answers to multiple-choice questions. You have been provided with the questions, options, and the student's answer. Carefully review the student's answer and provide a clear explanation on the correctness or incorrectness of their choice. Furthermore, explain why the other options are not the right answers."
Your output must be in the following JSON format: {'is_answer_correct': yes/no, 'answer': 'correct answer', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}"



## PREDICTION

In [9]:
def prepare_input(row, template="few_shot"):
    # d="Input: " + str({"Question": row['question'], "Options": eval(row['options'])}) + "\nOutput: "
    qstn=row['question']
    optn=row['options']
    d=f"Input: {{'Question': '{qstn}', 'Options': {optn}}}\nOutput: \n\n"
    if template=="zero_shot":
        d_ = zero_shot_prompt_template + "\n" + d
    else:
        d_ = few_shot_prompt_template + "\n" + d
    return d_

In [65]:
df.iloc[100, :]

id                             196e2700-d21e-42c0-91af-505c55e10900
dataset                                                   headqa_en
question          A patient of 25 years, during a tennis match, ...
options           {'0': 'III cranial pair.', '1': 'Optic chiasma...
correct_answer                                         Spinal bulb.
correct_index                                                     3
split_type                                                      val
subject_name                                               medicine
topic_name                                                      NaN
year                                                         2015.0
exam_name                                         Cuaderno_2015_1_M
student_answer                             Upper cervical ganglion.
student_index                                                     2
Name: 100, dtype: object

In [71]:
prompt=prepare_input(df.iloc[100, :])
print(generate(prompt))

As a medical teacher, you have the task of reviewing a medical student's answers to multiple-choice questions. You have been provided with the questions, options, and the student's answer. Carefully review the student's answer and provide a clear explanation on the correctness or incorrectness of their choice. Furthermore, explain why the other options are not the right answers."
Your output must be in the following JSON format: {'is_answer_correct': yes/no, 'answer': 'correct answer', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}"
Examples: 
Input : {'Question': 'A child has ptosis and poor levator function. What surgery will you do?', 'Options': {'0': 'Levator muscle resection', '1': 'Mullerectomy', '2': 'Fasanella Servat surgery', '3': 'Frontalis suspension surgery'}, 'correct_answer': 'Frontalis suspension surgery'}
Output: {'is_answer_correct': 'yes', 'correct answer': 'Frontalis suspension surgery', 'why_corre

In [14]:
final_preds = []
for ind, row in tqdm(df.iterrows()):
    print(ind)
    prompt = prepare_input(row)
    output = generate(prompt)
    final_preds.append(output)

0it [00:00, ?it/s]

0


1it [00:05,  5.58s/it]

1


2it [00:11,  6.02s/it]

...

18864it [37:33:23,  5.68s/it]

18864


18865it [37:33:28,  5.35s/it]

18865


18866it [37:33:35,  7.17s/it]


In [15]:
preds = pd.DataFrame(final_preds)
preds.to_csv('fct_predictions.csv', index=False)

## EVALUATION

In [46]:
ss_model = SentenceTransformer('all-MiniLM-L6-v2')

In [134]:
correct_score=1
incorrect_score=-0.25
fake_test_terms = ['i do not know', 
                   'conceding defeat', 
                   'admit', 
                   'none of the above',
                   'acknowled', 'irrelevant', 'fiction', 
                   'all of the above', 'ridiculous',
                   'nonsensical', 'no correct', 'absurd', 'defy', 'i don"t know.', 'defies', 'illogical', 'fifth option']

def calculate_score(correct, wrong):
    return (correct * correct_score + wrong * incorrect_score) / 100

def evaluate_answer(predicted, correct):
#     if str(predicted.lower()) != str(correct.lower()):
#         fuzzy_score = fuzz.ratio(predicted.lower(), correct.lower())/100.0
#         # emb1 = ss_model.encode(predicted.lower(), convert_to_tensor=True)
#         # emb2 = ss_model.encode(correct.lower(), convert_to_tensor=True)
#         # cosine_scores = util.pytorch_cos_sim(emb1, emb2)
        
#         if fuzzy_score > 0.6:
#             return True
#         else:
#             return False
#     else:
#         return True
    if (predicted.lower() == correct.lower()) or (predicted.lower() in correct.lower()) or (correct.lower() in predicted.lower()):
        return True
    else:
        return False
        
    
def create_dataframe(task_name, correct, wrong, score):
    total = correct + wrong
    df_dict = {'task_name': [task_name], 'total': [total], 'correct': [correct], 'wrong': [wrong], 'score': [score]}
    return pd.DataFrame(df_dict)
    
def handle_exceptions(sample, exception):
    print(exception)
    return 1
    
def is_correct(pred, rand_correct, gt):
    if (gt['correct_answer'].lower()==rand_correct.lower()) and pred['is_answer_correct'].lower()=='yes':
        return True
    else:
        return False
    
def reasoning_fct_eval(pred, gt, random_correct):
    correct, wrong, exception_count = 0, 0, 0

    possible_keys = ['correct_answer', 'answer', 'correct answer', 'corrent_answer', 'Correct Answer', 
                     'Answer', 'Correct_answer', "Correct answer"]

    for ind, sample in tqdm(enumerate(gt)):
        try:
            predicted_answer = None
            for key in possible_keys:
                if key in pred[ind]:
                    predicted_answer = pred[ind][key]
                    break

            if predicted_answer is None:
                if pred[ind]['is_answer_correct'] is not None:
                    if is_correct(pred[ind], random_correct[ind], sample):
                        print(f"Wohoooo IND::{ind}")
                        correct += 1
                    else:
                        wrong += 1
                else:
                    wrong += 1
                    raise KeyError("No valid key found in pred")
            else:
                if evaluate_answer(str(predicted_answer), sample['correct_answer']):
                    # print(f"Correct here: {predicted_answer} == {sample['correct_answer']}")
                    correct += 1
                else:
                    # print(f"Wrong here: {predicted_answer} == {sample['correct_answer']}")
                    wrong += 1

        except Exception as e:
            exception_count += handle_exceptions(sample, e)

    result = {
        "correct": correct,
        "wrong": wrong,
        "exception_count": exception_count
    }

    print(result)
    score = calculate_score(correct, wrong)  # calculate the score here
    return create_dataframe(task_name='FCT', correct=correct, wrong=wrong, score=score)
    
def extract_values(string):
    # Initialize variables with default values
    is_answer_correct = None
    correct_answer = None
    why_correct = None
    
    # Check if 'is_answer_correct' is present in the string
    if "'is_answer_correct': '" in string:
        is_answer_correct = string.split("'is_answer_correct': '")[1].split("'")[0]
    
    # Check if 'correct_answer' is present in the string
    if "'correct answer': '" in string:
        correct_answer = string.split("'correct answer': '")[1].split("'")[0]
    
    # Check if 'why_correct' is present in the string
    if "'why_correct': '" in string:
        why_correct = string.split("'why_correct': '")[1].split("'")[0]
    
    return is_answer_correct, correct_answer, why_correct

def extract_last_input(prompt):
    # Split the prompt by "Input:"
    inputs = prompt.split("Input:")[1:]
    
    # Get the last input
    last_input = inputs[-1].strip()
    
    # Check if 'correct answer' is present in the last input
    if "'correct answer'" in last_input:
        correct_answer = last_input.split("'correct answer': '")[1].split("'")[0]
    else:
        correct_answer = None
    
    return correct_answer

In [3]:
predictions = pd.read_csv('fct_predictions.csv')

In [105]:
'''
PREDICTIONS::

convert string outputs into dictionary
'''
pred_dict = []
for i, row in tqdm(predictions.iterrows()):
    try:
        model_out = row[0].split('Output:')[-1]
        is_correct, ans, why_correct = extract_values(model_out)
        pred_dict.append({'is_answer_correct':is_correct, 'correct answer':ans, 'why_correct':why_correct})
    except e:
        print(i)
        break

18866it [00:01, 17160.83it/s]


In [106]:
'''
GROUND-TRUTH::

get the ground-truth
'''
gt = pd.read_csv('reasoning_FCT.csv')

In [107]:
gt_values = [{'correct_answer':row['correct_answer'], 'correct_index':row['correct_index']} for ind, row in gt.iterrows()]

In [114]:
'''
GET THE RANDOMLY SUPPLIED CORRECT ANSWERS
'''
rand_correct_answers = [ast.literal_eval(gt['options'][i])['correct answer'] for i in tqdm(range(len(predictions)))]


100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 18866/18866 [00:00<00:00, 24682.73it/s]


In [117]:
rand_correct_answers[20]

'None'

In [63]:
gt_values[20]

{'correct_answer': 'Thyroid carcinoma', 'correct_index': 1}

In [62]:
pred_dict[20]

{'is_answer_correct': 'no',
 'correct answer': 'None',
 'why_correct': 'There was no mention of any primary cancer that would likely develop calcified pulmonary metastases. Therefore, none of the listed choices were correct.'}

In [135]:
res_df = reasoning_fct_eval(pred_dict, gt_values, rand_correct_answers)


18866it [00:00, 401150.48it/s]

'No valid key found in pred'
'No valid key found in pred'
'No valid key found in pred'
'No valid key found in pred'
'No valid key found in pred'
'No valid key found in pred'
'No valid key found in pred'
{'correct': 728, 'wrong': 18138, 'exception_count': 7}


In [136]:
res_df

task_name  total  correct  wrong   score
0       FCT  18866      728  18138 -38.065

In [133]:
(728/18866)*100

3.8587935969468883